In [1]:
from datetime import datetime
start_time  = datetime.now()
print("Last run: ", start_time)

Last run:  2023-05-13 07:22:00.289469


In [2]:
import urllib3, json
import pandas as pd 
http = urllib3.PoolManager() 
pd.set_option("display.max.columns", None) 
 
url = "https://litteraturbanken.se/api/get_authors"
r = http.request('GET', url)
data = json.loads(r.data)
dfLitt = pd.json_normalize(data["data"])

In [3]:
dfLittShowTrue = dfLitt[dfLitt["show"] == True].copy()
dfLittShowTrue.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3850 entries, 2 to 4922
Data columns (total 50 columns):
 #   Column                         Non-Null Count  Dtype  
---  ------                         --------------  -----  
 0   authorid                       3850 non-null   object 
 1   authorid_norm                  3850 non-null   object 
 2   db_checksum                    3850 non-null   object 
 3   db_timestamp                   3850 non-null   int64  
 4   doc_type                       3850 non-null   object 
 5   full_name                      3850 non-null   object 
 6   gender                         3850 non-null   object 
 7   imported                       3422 non-null   object 
 8   intro                          724 non-null    object 
 9   name_for_index                 3850 non-null   object 
 10  pictureinfo                    255 non-null    object 
 11  searchable                     3850 non-null   bool   
 12  show                           3850 non-null   b

In [4]:
# pip install sparqlwrapper
# https://rdflib.github.io/sparqlwrapper/

import sys,json
import pandas as pd 

from SPARQLWrapper import SPARQLWrapper, JSON

endpoint_url = "https://query.wikidata.org/sparql"

# 
query = """SELECT (REPLACE(STR(?item), ".*Q", "Q") AS ?WikidataID)  ?authorid ?SBL ?SKBL WHERE {
?item wdt:P31 wd:Q5.
?item wdt:P5101 ?authorid
OPTIONAL {?item wdt:P3217 ?SBL}
OPTIONAL {?item wdt:P4963 ?SKBL}
} order by ?authorid"""
 
    
def get_sparql_dataframe(endpoint_url, query):
    """
    Helper function to convert SPARQL results into a Pandas data frame.
    """
    user_agent = "salgo60/%s.%s" % (sys.version_info[0], sys.version_info[1])
 
    sparql = SPARQLWrapper(endpoint_url, agent=user_agent)
    sparql.setQuery(query)
    sparql.setReturnFormat(JSON)
    result = sparql.query()

    processed_results = json.load(result.response)
    cols = processed_results['head']['vars']
    out = []
    for row in processed_results['results']['bindings']:
        item = []
        for c in cols:
            item.append(row.get(c, {}).get('value'))
        out.append(item)

    return pd.DataFrame(out, columns=cols)

WDLittbanktot = get_sparql_dataframe(endpoint_url, query)

In [5]:
WDLittbanktot

WikidataID      authorid   SBL           SKBL
0      Q11967131        AasenE  None           None
1       Q4933592      AbeniusM  None  MargitAbenius
2      Q24680938  AbrahamssonA  None           None
3       Q4934135  AbrahamssonS  None           None
4        Q365923     AchariusE  5503           None
...          ...           ...   ...            ...
3482  Q108406266    ÖstergrenC  None           None
3483    Q6257795   ÖstergrenCL  None           None
3484  Q100752816        ÖstinO  None           None
3485    Q6258216       ÖstmanK  None           None
3486   Q11978200     ØverlandJ  None           None

[3487 rows x 4 columns]

In [6]:
# df = pd.merge(dfA, dfB, on=['a','b'], how="outer", indicator=True)
WDLittbank_WD_merge=  pd.merge(dfLittShowTrue,WDLittbanktot, how="outer", on='authorid',indicator=True)
WDLittbank_WD_merge.rename(columns={"_merge": "WD_Littbank_merge_Outer"},inplace = True)

WDLittbank_WD_merge["WD_Littbank_merge_Outer"].value_counts()



both          3319
left_only      531
right_only     168
Name: WD_Littbank_merge_Outer, dtype: int64

In [7]:
WDLittbank_WD_merge_Not_connected = \
WDLittbank_WD_merge[WDLittbank_WD_merge["WD_Littbank_merge_Outer"] == "left_only"].copy()

In [8]:
WDLittbank_WD_merge_Not_connected

authorid authorid_norm                       db_checksum  \
7          Addäos        Addaos  da5e35f5f2e32602a17344e44b2b6e93   
30       AhlbergL      AhlbergL  ee16e9ff206c29114ebb85c687f26a3d   
39        AhlmanC       AhlmanC  ded5b5ffeea552a3c1ea1778d4430364   
49     AhrenbergB    AhrenbergB  b1741fb810e253a036639d61e7a3563f   
66    AllvarssonA   AllvarssonA  3dfce487ff899fd930a9216c072f4f21   
...           ...           ...                               ...   
3815   ÅkerlundPA    AkerlundPA  305970795ebaa9fc00e54d3889a241f1   
3819       ÅlundP        AlundP  7e20f1ee10e297c8935b8413bff60610   
3838      OhmanFA       OhmanFA  eed1bf5666f0b20a897d2dd6ac37270c   
3845  ÖstergrenPJ   OstergrenPJ  27ee5cfe5cf3d88be34963b41f68331f   
3847      ÖstmanC       OstmanC  6a20a9700a39284e25991764ae0d769a   

      db_timestamp doc_type           full_name     gender    imported intro  \
7     1.682496e+12   author              Addäos       male  2014-08-22  None   
30    1.682496e+12   author      Ludvig Ahlberg       male  2021-03-01  None   
39    1.682496e+12   author      Carl O. Ahlman       male  2019-02-25  None   
49    1.682496e+12   author    Bertha Ahrenberg     female  2022-01-31  None   
66    1.682496e+12   author   Anders Allvarsson       male  2023-03-27  None   
...            ...      ...                 ...        ...         ...   ...   
3815  1.682496e+12   author      P. A. Åkerlund  not known  2021-04-06  None   
3819  1.682496e+12   author        Paulus Ålund       male  2019-02-25  None   
3838  1.682496e+12   author  Frans August Öhman       male         NaN  None   
3845  1.682496e+12   author     P. J. Östergren       male  2021-11-29  None   
3847  1.682496e+12   author        Carin Östman     female  2014-02-11  None   

           name_for_index pictureinfo searchable  show     surname  \
7                  Addäos        None      False  True      Addäos   
30        Ahlberg, Ludvig        None       True  True     Ahlberg   
39        Ahlman, Carl O.        None      False  True      Ahlman   
49      Ahrenberg, Bertha        None       True  True   Ahrenberg   
66     Allvarsson, Anders        None       True  True  Allvarsson   
...                   ...         ...        ...   ...         ...   
3815      Åkerlund, P. A.        None       True  True    Åkerlund   
3819        Ålund, Paulus        None       True  True       Ålund   
3838  Öhman, Frans August        None      False  True       Öhman   
3845     Östergren, P. J.        None       True  True   Östergren   
3847        Östman, Carin        None       True  True      Östman   

         updated birth.date birth.plain death.date death.plain librisid  \
7     2016-04-12       -350        0000        NaN        0000      NaN   
30    2021-03-01        NaN        1809       1888        1888      NaN   
39    2019-02-25       1830        0000        NaN         NaN      NaN   
49    2022-01-31       1851        0000        NaN        0000      NaN   
66    2023-03-27       1871        0000        NaN        0000      NaN   
...          ...        ...         ...        ...         ...      ...   
3815  2021-04-06       1843        0000        NaN        0000      NaN   
3819  2019-02-25       1820        0000        NaN         NaN      NaN   
3838         NaN       1821        1821       1892        1892      NaN   
3845  2021-11-29       1870        0000        NaN        0000      NaN   
3847  2014-03-17       1958        1958        NaN         NaN      NaN   

     wikidata.birthplace wikidata.birthplace_label wikidata.deathplace  \
7                    NaN                       NaN                 NaN   
30                   NaN                       NaN                 NaN   
39                   NaN                       NaN                 NaN   
49                   NaN                       NaN                 NaN   
66                   NaN                       NaN                 NaN   
...                  ...         

In [9]:
WDLittbank_WD_merge_Not_connected[WDLittbank_WD_merge_Not_connected['librisid']. 
                                  notna()][["authorid","librisid","show","full_name"]]

authorid         librisid  show            full_name
165   ArfwidssonN  hftwzq01397wbbd  True      Nils Arfwidsson
1517      Homeros  0xbdfjvj5rjnrc0  True              Homeros
3515    ValbäckFJ  gdsvzxn032qd1hm  True  Frans Johan Valbäck
3679    WhitlockA  97mpsnpt0lf558s  True        Anna Whitlock

In [10]:
WDLittbank_WD_merge_Not_connected.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 531 entries, 7 to 3847
Data columns (total 54 columns):
 #   Column                         Non-Null Count  Dtype   
---  ------                         --------------  -----   
 0   authorid                       531 non-null    object  
 1   authorid_norm                  531 non-null    object  
 2   db_checksum                    531 non-null    object  
 3   db_timestamp                   531 non-null    float64 
 4   doc_type                       531 non-null    object  
 5   full_name                      531 non-null    object  
 6   gender                         531 non-null    object  
 7   imported                       409 non-null    object  
 8   intro                          21 non-null     object  
 9   name_for_index                 531 non-null    object  
 10  pictureinfo                    4 non-null      object  
 11  searchable                     531 non-null    object  
 12  show                           531 

In [11]:
WDLittbank_WD_merge_Not_connected["librisid"].value_counts()

hftwzq01397wbbd    1
0xbdfjvj5rjnrc0    1
gdsvzxn032qd1hm    1
97mpsnpt0lf558s    1
Name: librisid, dtype: int64

In [12]:
WDLittbank_WD_merge_Not_connected[WDLittbank_WD_merge_Not_connected["librisid"] =="20dgkckl01lmd80"]

Empty DataFrame
Columns: [authorid, authorid_norm, db_checksum, db_timestamp, doc_type, full_name, gender, imported, intro, name_for_index, pictureinfo, searchable, show, surname, updated, birth.date, birth.plain, death.date, death.plain, librisid, wikidata.birthplace, wikidata.birthplace_label, wikidata.deathplace, wikidata.deathplace_label, wikidata.image, wikidata.sbl_link, wikidata.skbl_link, wikidata.sol_link, wikidata.wikidata_id, wikidata.wikipedia, db_timestamp_updated, intro_text, popularity, pseudonym, dramawebben.intro, dramawebben.intro_author, dramawebben.intro_author_norm, dramawebben.legacy_url, dramawebben.picture, sources, other_name, intro_author, intro_author_norm, dramawebben.picture_info, picture, bibliography, external_ref, presentation, seemore, dramawebben.sources, WikidataID, SBL, SKBL, WD_Littbank_merge_Outer]
Index: []

In [13]:
WDLittbank_WD_merge_Not_connected["wikidata.sbl_link"].value_counts()

Series([], Name: wikidata.sbl_link, dtype: int64)

In [14]:
#WDLittbank_WD_merge_Not_connected["sources"].value_counts()

In [15]:
#WDLittbank_WD_merge_Not_connected["popularity"].value_counts()

In [16]:
# WDLittbank_WD_merge_Not_connected["intro_text"].value_counts()

### check WD

In [17]:
# df = pd.merge(dfA, dfB, on=['a','b'], how="outer", indicator=True)
WDLittbank_WD_onWD_merge=  pd.merge(dfLittShowTrue,WDLittbanktot, how="outer", on='authorid',indicator=True)
WDLittbank_WD_onWD_merge.rename(columns={"_merge": "WD_Littbank_merge_Outer"},inplace = True)

WDLittbank_WD_onWD_merge["WD_Littbank_merge_Outer"].value_counts()


both          3319
left_only      531
right_only     168
Name: WD_Littbank_merge_Outer, dtype: int64